In [1]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from tab_transformer_pytorch import TabTransformer, FTTransformer
from preprocessing import get_features_and_target
from sklearn.preprocessing import LabelEncoder
from RMSELoss import RMSELoss
import plotly.graph_objects as go

# Getting Dataframe

In [2]:
train_df = pd.read_csv("data/train_data.csv")
dev_df = pd.read_csv("data/development_data.csv")

target_column = "PullTest (N)"  

x_train, y_train = get_features_and_target(train_df, target_column)
x_dev, y_dev = get_features_and_target(dev_df, target_column)



# Encode Categorical_Features

In [3]:
# Define the categorical features
categorical_features = ["Material"]

le = LabelEncoder()

for feature in categorical_features:
    x_train[feature] = le.fit_transform(x_train[feature])
    x_dev[feature] = le.transform(x_dev[feature])  

# Split Categorical_Features

In [4]:
# Drop categorical features to get the continuous features
x_train_numerical_features = x_train.drop(categorical_features, axis=1)
x_dev_numerical_features = x_dev.drop(categorical_features, axis=1)

# Seperate the categorical features
x_train_categorical_features = x_train[categorical_features]
x_dev_categorical_features = x_dev[categorical_features]

# Change df into Tensors

In [5]:
train_tensor = torch.tensor(x_train.to_numpy(), dtype=torch.float)
x_train_numer_tensor = torch.tensor(x_train_numerical_features.to_numpy(),dtype=torch.float)
x_dev_numer_tensor = torch.tensor(x_dev_numerical_features.to_numpy(),dtype=torch.float)
y_train_tensor = torch.tensor(y_train.to_numpy(), dtype=torch.float)

dev_tensor = torch.tensor(x_dev.to_numpy(), dtype=torch.float)
x_train_categorical_features_tensor = torch.tensor(x_train_categorical_features.to_numpy(),dtype=torch.long)
x_dev_categorical_features_tensor = torch.tensor(x_dev_categorical_features.to_numpy(),dtype=torch.long)
y_dev_tensor = torch.tensor(y_dev.to_numpy(), dtype=torch.float)

from torch.utils.data import TensorDataset,DataLoader

train_ds = TensorDataset(
    x_train_categorical_features_tensor,
    x_train_numer_tensor,
    y_train_tensor
)
val_ds = TensorDataset(
    x_dev_categorical_features_tensor,
    x_dev_numer_tensor,
    y_dev_tensor
)
g = torch.Generator()
g.manual_seed(42)
train_loader = DataLoader(train_ds, batch_size=32, shuffle=True, generator= g)
val_loader   = DataLoader(val_ds,   batch_size=32)



# Check Tensors


In [6]:
#torch.set_printoptions(sci_mode=False, precision=3)
#print(x_train_numer_tensor)

# Define Model

In [82]:
# categories is defined as a tuple, we only have one categorical feature "Material"
# the second parameter has to be empty for the model to work correctly
# in hard numbers this is displaying (1,)
model = FTTransformer(
    categories=(x_train_categorical_features.shape[1],),
    num_continuous=x_train_numerical_features.shape[1],
    dim=8,
    dim_out=1,
    depth=4,
    heads=4,
    attn_dropout=0.3,
    ff_dropout=0.3
)

# Physical Epoch


In [83]:
# Make sure these indices match the *positions* of your “Thickness A (mm)” 
# and “Thickness B (mm)” in the x_cont tensor!
# If you built x_cont from a DataFrame like:
#    cont_cols = ["Thickness A (mm)", "Thickness B (mm)", …]
# then idxA = 0, idxB = 1
idxA, idxB = 5, 6  

def physics_pull_force(x_cont):
    # x_cont: [B, num_cont_features]
    A = x_cont[:, idxA]               # shape [B]
    B = x_cont[:, idxB]               # shape [B]

    # element‐wise minimum of each row
    # torch.minimum was added in PyTorch 1.7+
    t = torch.minimum(A, B)           # shape [B]
    # now compute f_phys = (π/4)*(5*√t)^2*(0.6*365)
    # keep it as [B] so we can later unsqueeze to [B,1]
    return ((torch.pi / 4) * (4 * torch.sqrt(t)).pow(2) * (0.8 * 365))


def train_one_epoch(train_loader):
    total_combined = 0.0
    total_data     = 0.0
    total_phys     = 0.0

    for x_cat, x_cont, y in train_loader:
        optimizer.zero_grad()

        # ensure y is [B,1]
        y = y.unsqueeze(-1)
        # forward
        pred = model(x_cat, x_cont)       # [B,1]

        # data loss
        data_loss = criterion(pred, y)

        # physics target (no grads needed for f_phys)
        with torch.no_grad():
            f_phys = physics_pull_force(x_cont).unsqueeze(-1)    # [B]
            
        # MSE to the physics‐based target
        phys_loss = criterion(pred, f_phys)

        # combined loss
        loss = data_loss + lambda_phys * phys_loss
        loss.backward()
        optimizer.step()

        total_combined += loss.item()
        total_data     += data_loss.item()
        total_phys     += phys_loss.item()


    return  (total_combined / len(train_loader),
             total_data / len(train_loader),
             total_phys / len(train_loader))



# Physical Training

In [84]:
from datetime import datetime

criterion = RMSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.00025)

#Changeable Parameters
# ----------------------------------------------------#
#Model description for saving
model_description    = 'lr0.00025_8_1_4_4_.3_.3PhysicsLambda8'

# Number of epochs to train
EPOCHS = 20000

# Hyperparam to weight the physics loss
lambda_phys = 8
#-----------------------------------------------------#

# Lists to store per‐epoch losses
train_data_losses       = []
train_phys_losses       = []
train_dataphys_losses   = []
val_data_losses         = []
val_phys_losses         = []
val_dataphys_losses     = []

best_vloss   = float('inf')
last_ckpt  = None
timestamp    = datetime.now().strftime('%Y%m%d')



for epoch in range(EPOCHS):
    print(f'\nEPOCH {epoch+1}/{EPOCHS}')

    # --------------------
    # 1) TRAINING PHASE
    # --------------------
    model.train()
    train_combined, train_data, train_phys = train_one_epoch(train_loader)

    train_data_losses.append(train_data)
    train_phys_losses.append(train_phys)
    train_dataphys_losses.append(train_combined)
    print(f'train loss: {train_combined:.4f}')

    # --------------------
    # 2) VALIDATION PHASE
    # --------------------
    model.eval()
    
    val_loss = 0.0
    phys_loss = 0.0
    with torch.no_grad():
        for x_cat, x_cont, y in val_loader:
            y = y.unsqueeze(-1)
            pred = model(x_cat, x_cont)

            # 1) data‐driven loss
            val_loss += criterion(pred, y).item()

            A = x_cont[:, idxA]
            B = x_cont[:, idxB]
            t = torch.minimum(A, B)
            f_phys = physics_pull_force(x_cont)    # [B]
            f_phys = f_phys.unsqueeze(-1) 


            phys_loss += criterion(pred, f_phys).item()

    avg_vloss = val_loss / len(val_loader)
    avg_phys  = phys_loss  / len(val_loader)
    avg_total = avg_vloss +  lambda_phys * avg_phys

    val_data_losses.append(avg_vloss)
    val_phys_losses.append(avg_phys)
    val_dataphys_losses.append(avg_total)

    print(f'valid loss: {avg_total:.4f}')
    

    # --------------------
    # 3) CHECKPOINTING
    # --------------------
    if (epoch + 1) % 100 == 0 and avg_total < best_vloss:
        if last_ckpt is not None:
            os.remove(last_ckpt)

        best_vloss = avg_total
        ckpt_path = f'trained_models/physical_loss_training/model_{model_description}_date_{timestamp}_epoch{epoch+1}.pt'
        torch.save(model.state_dict(), ckpt_path)
        last_ckpt = ckpt_path



EPOCH 1/20000
train loss: 21843.3989
valid loss: 21954.4386

EPOCH 2/20000
train loss: 21797.8707
valid loss: 21952.7898

EPOCH 3/20000
train loss: 21885.9219
valid loss: 21951.0352

EPOCH 4/20000
train loss: 21871.2975
valid loss: 21949.8189

EPOCH 5/20000
train loss: 21791.9722
valid loss: 21949.5576

EPOCH 6/20000
train loss: 21821.7973
valid loss: 21949.3360

EPOCH 7/20000
train loss: 21796.2513
valid loss: 21949.0935

EPOCH 8/20000
train loss: 21795.8813
valid loss: 21948.8687

EPOCH 9/20000
train loss: 21823.1228
valid loss: 21948.6835

EPOCH 10/20000
train loss: 21786.9644
valid loss: 21948.5283

EPOCH 11/20000
train loss: 21849.9434
valid loss: 21948.3791

EPOCH 12/20000
train loss: 21871.3056
valid loss: 21948.2310

EPOCH 13/20000
train loss: 21828.7507
valid loss: 21948.0860

EPOCH 14/20000
train loss: 21832.1191
valid loss: 21947.9411

EPOCH 15/20000
train loss: 21853.6825
valid loss: 21947.7948

EPOCH 16/20000
train loss: 21795.3320
valid loss: 21947.6497

EPOCH 17/20000
t

KeyboardInterrupt: 

Only Physics Lambda 1:

train loss: 121.9670
valid loss: 148.8158

In [85]:
import plotly.graph_objects as go

fig = go.Figure()

# Training loss trace
fig.add_trace(go.Scatter(
    y=train_data_losses,
    mode="lines+markers",
    name="Train Data Loss",
    line=dict(color="lightblue", width=2),
    marker=dict(size=4)
))

# Training loss trace
fig.add_trace(go.Scatter(
    y=train_phys_losses,
    mode="lines+markers",
    name="Train Physical Loss",
    line=dict(color="royalblue", width=2),
    marker=dict(size=4)
))

# Training loss trace
fig.add_trace(go.Scatter(
    y=train_dataphys_losses,
    mode="lines+markers",
    name="Train Data+Physical Loss",
    line=dict(color="black", width=2),
    marker=dict(size=4)
))

# Validation loss trace
fig.add_trace(go.Scatter(
    y=val_data_losses,
    mode="lines+markers",
    name="Validation Data Loss",
    line=dict(color="orange", width=2),
    marker=dict(size=4)
))

# Validation loss trace
fig.add_trace(go.Scatter(
    y=val_phys_losses,
    mode="lines+markers",
    name="Validation Physical Loss",
    line=dict(color="tomato", width=2),
    marker=dict(size=4)
))

# Validation loss trace
fig.add_trace(go.Scatter(
    y=val_dataphys_losses,
    mode="lines+markers",
    name="Validation Data+Physical Loss",
    line=dict(color="firebrick", width=2),
    marker=dict(size=4)
))

# Layout
fig.update_layout(
    title="Training & Validation Loss over Epochs  - lr0.00025_8_1_4_4_.3_.3 - Physics Lambda 8",
    xaxis_title="Epoch",
    yaxis_title="Loss",
    xaxis=dict(
        tickmode='array',
        tickvals=list(range(0, 10500, 500)),  # Show ticks every 100 epochs
        tickfont=dict(size=10)
    ),
    template="plotly_white",
    legend=dict(
        x=0.7,        # push legend past the right edge
        y=1,
        xanchor="left",
        borderwidth=1
    ),
    margin=dict(t=60, b=40)  # give extra room on right for the legend
)

fig.show()


In [86]:
import plotly.graph_objects as go

epochs = list(range(1, len(train_data_losses) + 1))

fig = go.Figure()

# Training loss trace
fig.add_trace(go.Scatter(
    x=epochs,
    y=train_data_losses,
    mode="lines",
    name="Train Data Loss",
    line=dict(color="lightblue", width=2)
))

fig.add_trace(go.Scatter(
    x=epochs,
    y=train_phys_losses,
    mode="lines",
    name="Train Physical Loss",
    line=dict(color="royalblue", width=2)
))

fig.add_trace(go.Scatter(
    x=epochs,
    y=train_dataphys_losses,
    mode="lines",
    name="Train Data+Physical Loss",
    line=dict(color="black", width=2)
))

# Validation loss trace
fig.add_trace(go.Scatter(
    x=epochs,
    y=val_data_losses,
    mode="lines",
    name="Validation Data Loss",
    line=dict(color="orange", width=2, dash="dash")
))

fig.add_trace(go.Scatter(
    x=epochs,
    y=val_phys_losses,
    mode="lines",
    name="Validation Physical Loss",
    line=dict(color="tomato", width=2, dash="dash")
))

fig.add_trace(go.Scatter(
    x=epochs,
    y=val_dataphys_losses,
    mode="lines",
    name="Validation Data+Physical Loss",
    line=dict(color="firebrick", width=2, dash="dash")
))

# Layout enhancements
fig.update_layout(
    title="Training & Validation Loss over 10 000 Epochs - lr0.00025_8_1_4_4_.3_.3 - Physics Lambda 8",
    xaxis_title="Epoch",
    yaxis_title="Loss",
    xaxis=dict(
        tickmode='array',
        tickvals=list(range(0, 10500, 500)),  # Show ticks every 100 epochs
        tickfont=dict(size=10)
    ),
    yaxis=dict(
        tickformat=".2e" if max(train_data_losses + val_data_losses) > 1e4 else ".4f",  # Dynamic formatting
        gridcolor="lightgray"
    ),
    legend=dict(
        x=0.7,        # push legend past the right edge
        y=1,
        xanchor="left",
        borderwidth=1
    ),
    
    template="plotly_white",
    margin=dict(t=60, b=40)
)

fig.show()


In [87]:
from sklearn.metrics import r2_score


r2 = r2_score(y, pred)
print(f"R² = {r2:.4f}")

R² = -24.5461


In [ ]:
import numpy as np
from sklearn.metrics import mean_absolute_error, mean_squared_error

# Collect predictions and true values from the validation set
model.eval()
all_preds = []
all_targets = []

with torch.no_grad():
    for x_categ, x_numer, y_train in val_loader:
        preds = model(x_categ, x_numer).squeeze().cpu().numpy()
        all_preds.extend(preds)
        all_targets.extend(y_train.cpu().numpy())

all_preds = np.array(all_preds)
all_targets = np.array(all_targets)

# Inverse-transform predictions and targets to original units
preds_orig = y_train
targets_orig = y_train

# Calculate MAE and RMSE in original units
mae = mean_absolute_error(targets_orig, preds_orig)
rmse = np.sqrt(mean_squared_error(targets_orig, preds_orig))

print(f"MAE (original units): {mae:.2f}")
print(f"RMSE (original units): {rmse:.2f}")

MAE (original units): 0.00
RMSE (original units): 0.00
